# Getting Event and Market Data

## 1. Extraction of ALL EVENTS AVAILABLE and the respective markets from Kalshi

Google Collab with useful Python Code for Kalshi: https://colab.research.google.com/drive/1yyFKssS6pT8LQPDJ43xLwAvcH5JEMfit?usp=sharing#scrollTo=WKr-ZecrySoF

Other useful repositories for Polymarket vs Kalshi arbitrage: https://github.com/pmxt-dev/pmxt \
https://www.reddit.com/r/algotrading/comments/1qbq7j1/automating_the_prediction_market_arb/ \
https://github.com/Kalshi/kalshi-starter-code-python/tree/main \
https://www.youtube.com/watch?v=E2mgWN4ReqQ \
https://docs.kalshi.com/api-reference/market/get-series-list

In [ ]:
# The url link here will give a useful overview of the available parameters of events/markets that can be used below (chrome)
import requests
r = requests.get("https://api.elections.kalshi.com/trade-api/v2/events?with_nested_markets=true&status=open")
response = r.json()

response

{'cursor': 'CgYI8Nj99wYSC1NFTkFURVBBLTI4',
 'events': [{'available_on_brokers': False,
   'category': 'World',
   'collateral_return_type': '',
   'event_ticker': 'KXELONMARS-99',
   'mutually_exclusive': False,
   'series_ticker': 'KXELONMARS',
   'strike_period': '',
   'sub_title': 'Before 2099',
   'title': 'Will Elon Musk visit Mars in his lifetime?'},
  {'available_on_brokers': False,
   'category': 'World',
   'collateral_return_type': 'MECNET',
   'event_ticker': 'KXNEWPOPE-70',
   'mutually_exclusive': True,
   'series_ticker': 'KXNEWPOPE',
   'strike_period': '',
   'sub_title': 'Before 2070',
   'title': 'Who will the next Pope be?'},
  {'available_on_brokers': False,
   'category': 'Climate and Weather',
   'collateral_return_type': '',
   'event_ticker': 'KXWARMING-50',
   'mutually_exclusive': False,
   'series_ticker': 'KXWARMING',
   'strike_period': '',
   'sub_title': 'Before 2050',
   'title': 'Will the world pass 2 degrees Celsius over pre-industrial levels before 2

Filter on Events Containing Fed and Rate

Now we don't want to bet on everything, let's select something we're interested in at this time. Going to filter on those that are related to Fed rate cuts

In [2]:
import requests
from collections import defaultdict

KALSHI_API = "https://api.elections.kalshi.com/trade-api/v2"

# -------- FETCH ALL ACTIVE EVENTS WITH NESTED MARKETS --------
all_events = []
cursor = None
limit = 50
while True:
    params = {
        "status": "open",
        "with_nested_markets": True,
        "limit": limit,
        "with_milestones": True
    }
    if cursor:
        params["cursor"] = cursor
    
    response = requests.get(f"{KALSHI_API}/events", params=params)
    data = response.json()
    events = data.get('events', [])
    
    if not events:
        break
    
    all_events.extend(events)
    cursor = data.get('cursor')
    if not cursor:
        break

# -------- GROUP EVENTS BY CATEGORY  --------
events_by_category = defaultdict(list)
for event in all_events:
    category = event.get("category", "N/A")
    events_by_category[category].append(event)

# -------- PRINT EVENTS + MARKETS + OUTCOMES --------
for category, events in events_by_category.items():
    print(f"\n=== TICKER {category} ({len(events)} events) ===")

    for event in events:
        event_id = event.get("event_ticker", "N/A")  # Using event_ticker as event ID
        event_title = event.get("title", "N/A")
        category = event.get("category", "N/A")

        print(f"\n▶ Event [{event_id}] {event_title} ({category})")

        markets = event.get("markets", [])

        if not markets:
            print("  (No available markets)")
            continue

        print(f"  Available markets ({len(markets)}):")

        for market in markets:
            market_id = market.get("ticker", "N/A")
            market_title = market.get("yes_sub_title", "N/A")
            last_traded_price_yes = market.get("last_price_dollars", "N/A")  # Using title as equivalent to question
            outcome_prices = {
                "PriceYesBuy": market.get("yes_bid_dollars", "N/A"),
                "PriceNoBuy": market.get("no_bid_dollars", "N/A")
            }

            print(
                f"    - Market [{market_id}] {market_title} | "
                f"BuyOrderBook: {outcome_prices} | "
                f"YesChance: {last_traded_price_yes}" 
            )


=== TICKER World (33 events) ===

▶ Event [KXELONMARS-99] Will Elon Musk visit Mars in his lifetime? (World)
  Available markets (1):
    - Market [KXELONMARS-99] Mars | BuyOrderBook: {'PriceYesBuy': '0.0600', 'PriceNoBuy': '0.9000'} | YesChance: 0.0600

▶ Event [KXNEWPOPE-70] Who will the next Pope be? (World)
  Available markets (7):
    - Market [KXNEWPOPE-70-PPAR] Pietro Parolin | BuyOrderBook: {'PriceYesBuy': '0.0600', 'PriceNoBuy': '0.9100'} | YesChance: 0.0900
    - Market [KXNEWPOPE-70-PERD] Peter Erdo | BuyOrderBook: {'PriceYesBuy': '0.0300', 'PriceNoBuy': '0.9500'} | YesChance: 0.0300
    - Market [KXNEWPOPE-70-MZUP] Matteo Zuppi | BuyOrderBook: {'PriceYesBuy': '0.0400', 'PriceNoBuy': '0.9300'} | YesChance: 0.0400
    - Market [KXNEWPOPE-70-LANT] Luis Antonio Tagle | BuyOrderBook: {'PriceYesBuy': '0.0500', 'PriceNoBuy': '0.9200'} | YesChance: 0.0700
    - Market [KXNEWPOPE-70-FAMB] Fridolin Ambongo | BuyOrderBook: {'PriceYesBuy': '0.0300', 'PriceNoBuy': '0.9500'} | YesChance

## 2. For each available SPORT, all events with the respective markets will be extracted

In [ ]:
# Use url link here on chrome to get an understanding of the sport parameters and settings
url = "https://api.elections.kalshi.com/trade-api/v2/search/filters_by_sport"

response = requests.get(url)

print(response.text)

{"filters_by_sports":{"All sports":{"competitions":{},"scopes":["Games","Futures","1st Half Spread","1st Half Total","1st Half Winner","Awards","Blocks","Combo","Conference","Divisions","Finishing Position","Goalscorer","Group Qualifiers","Group Winner","League Leader","Map Winner","Receiving Yards","Rushing Yards","Steals","To Advance","Total Maps","Wins","Events"]},"Baseball":{"competitions":{"Pro Baseball":{"scopes":["Futures","Win totals","Divisions","Events"]}},"scopes":["Futures","Divisions","Wins","Events"]},"Basketball":{"competitions":{"Chinese Basketball Association":{"scopes":["Games"]},"College Basketball (M)":{"scopes":["Games","Futures","Awards","Conference"]},"College Basketball (W)":{"scopes":["Games","Futures"]},"EuroCup":{"scopes":["Games"]},"Euroleague":{"scopes":["Games"]},"FIBA Champions League":{"scopes":["Games"]},"LNB Elite":{"scopes":["Games"]},"Liga Nacional de Basquetbol":{"scopes":["Games"]},"NBL Australia":{"scopes":["Games"]},"Pro Basketball (M)":{"scopes"

In [7]:
import requests

url = "https://api.elections.kalshi.com/trade-api/v2/search/tags_by_categories"

response = requests.get(url)

print(response.text)

{"tags_by_categories":{"Climate and Weather":["Daily temperature","Snow and rain","Climate change","High temp","Natural disasters","Hurricanes"],"Companies":["KPIs","Product launches","Elon Musk","CEOs","Layoffs"],"Crypto":["BTC","Hourly","ETH","SOL","Pre-Market","15 min","Dogecoin","SHIBA"],"Economics":["Fed","Oil and energy","Growth","Inflation","Employment","Housing","Mortgages"],"Elections":["International elections"],"Entertainment":["Awards","Movies","Music","Music charts","Television","Video games","Rotten Tomatoes","Live Music"],"Financials":["S\u0026P","Daily","EUR/USD","Nasdaq","Treasuries","USD/JPY"],"Mentions":null,"Politics":["US Elections","Primaries","Trump","Foreign Elections","House","International","Congress","SCOTUS \u0026 courts","Local","Recurring"],"Science and Technology":["AI","Space","Energy"],"Social":null,"Sports":["Soccer","Basketball","Football","Baseball","Hockey","Golf","Esports","Tennis","UFC","MMA","Cricket","Motorsport","Chess","Table Tennis"],"Transpo

### Here we only extract SOCCER GAMES and respective events

In [2]:
import requests
#from collections import defaultdict

KALSHI_API = "https://api.elections.kalshi.com/trade-api/v2"

# -------- FETCH SOCCER SERIES TICKERS --------
response = requests.get(f"{KALSHI_API}/series", params={"category": "Sports", "tags": "Soccer"})
series_data = response.json().get('series', [])
soccer_tickers = [s.get("ticker") for s in series_data if s.get("ticker")]

print(f"Found {len(soccer_tickers)} Soccer Events")

# -------- FETCH EVENTS FOR EACH SOCCER SERIES TICKER --------
all_events = []
for ticker in soccer_tickers:
    cursor = None
    limit = 200
    while True:
        params = {
            "status": "open",
            "series_ticker": ticker,
            "with_nested_markets": True,
            "limit": limit,
            "with_milestones": True
        }
        if cursor:
            params["cursor"] = cursor
        
        response = requests.get(f"{KALSHI_API}/events", params=params)
        data = response.json()
        events = data.get('events', [])
        
        if not events:
            break
        
        all_events.extend(events)
        cursor = data.get('cursor')
        if not cursor:
            break

for event in all_events:
    event_series = event.get("series_ticker", "N/A")
    event_subtitle = event.get("sub_title", "N/A")
    event_id = event.get("event_ticker", "N/A")  # Using event_ticker as event ID
    event_title = event.get("title", "N/A")
    category = event.get("category", "N/A")

    print(f"\n▶ Event [{event_id}] ({event_series}) ({event_subtitle}) {event_title} ({category})")

    markets = event.get("markets", [])

    if not markets:
        print("  (No available markets)")
        continue

    print(f"  Available markets ({len(markets)}):")

    for market in markets:
        market_ticker = market.get("event_ticker")
        market_id = market.get("ticker", "N/A")
        market_title = market.get("yes_sub_title", "N/A")
        last_traded_price_yes = market.get("last_price_dollars", "N/A")  # Using title as equivalent to question
        outcome_prices = {
                "PriceYesBuy": market.get("yes_bid_dollars", "N/A"),
                "PriceNoBuy": market.get("no_bid_dollars", "N/A")
            }

        print(
                f"    - Market [{market_id}] ({market_ticker}) {market_title} | "
                f"OrderBook: {outcome_prices} | "
                f"Yes_Chance: {last_traded_price_yes}" 
            )

Found 195 Soccer Events

▶ Event [KXLIGAPORTUGALGAME-26JAN25BRAALV] (KXLIGAPORTUGALGAME) (BRA vs ALV (Jan 25)) Braga vs Alverca (Sports)
  Available markets (3):
    - Market [KXLIGAPORTUGALGAME-26JAN25BRAALV-TIE] (KXLIGAPORTUGALGAME-26JAN25BRAALV) Tie | OrderBook: {'PriceYesBuy': '0.1900', 'PriceNoBuy': '0.7800'} | Yes_Chance: 0.0000
    - Market [KXLIGAPORTUGALGAME-26JAN25BRAALV-BRA] (KXLIGAPORTUGALGAME-26JAN25BRAALV) Braga | OrderBook: {'PriceYesBuy': '0.6700', 'PriceNoBuy': '0.3000'} | Yes_Chance: 0.7000
    - Market [KXLIGAPORTUGALGAME-26JAN25BRAALV-ALV] (KXLIGAPORTUGALGAME-26JAN25BRAALV) Alverca | OrderBook: {'PriceYesBuy': '0.1000', 'PriceNoBuy': '0.8900'} | Yes_Chance: 0.1100

▶ Event [KXLIGAPORTUGALGAME-26JAN25FAMTON] (KXLIGAPORTUGALGAME) (FAM vs TON (Jan 25)) Famalicao vs Tondela (Sports)
  Available markets (3):
    - Market [KXLIGAPORTUGALGAME-26JAN25FAMTON-TON] (KXLIGAPORTUGALGAME-26JAN25FAMTON) Tondela | OrderBook: {'PriceYesBuy': '0.1400', 'PriceNoBuy': '0.8400'} | Yes_C

### Here we extract ALL MARKETS OF ALL SPORT DIVIDED BY CATEGORY

In [1]:
import requests
from collections import defaultdict

KALSHI_API = "https://api.elections.kalshi.com/trade-api/v2"

# -------- FETCH ALL SPORTS --------
response = requests.get(f"{KALSHI_API}/search/filters_by_sport")
filters_data = response.json()
all_sports = [sport for sport in filters_data.get("sport_ordering", []) if sport != "All sports"]

print(f"Found {len(all_sports)} sports: {all_sports}")

# -------- LOOP OVER EACH SPORT --------
for sport in all_sports:
    print(f"\n\n========== SPORT: {sport} ==========")
    
    # -------- FETCH SERIES TICKERS FOR THIS SPORT --------
    response = requests.get(f"{KALSHI_API}/series", params={"category": "Sports", "tags": sport})
    series_data = response.json().get('series', [])
    sport_tickers = [s.get("ticker") for s in series_data if s.get("ticker")]
    
    print(f"Found {len(sport_tickers)} {sport} series tickers")
    
    # -------- FETCH EVENTS FOR EACH TICKER IN THIS SPORT --------
    all_events = []
    for ticker in sport_tickers:
        cursor = None
        limit = 200
        while True:
            params = {
                "status": "open",
                "series_ticker": ticker,
                "with_nested_markets": True,
                "limit": limit,
                "with_milestones": True
            }
            if cursor:
                params["cursor"] = cursor
            
            response = requests.get(f"{KALSHI_API}/events", params=params)
            data = response.json()
            events = data.get('events', [])
            
            if not events:
                break
            
            all_events.extend(events)
            cursor = data.get('cursor')
            if not cursor:
                break
    
    # -------- PRINT EVENTS + MARKETS FOR THIS SPORT --------
    for event in all_events:
        event_id = event.get("event_ticker", "N/A")
        event_title = event.get("title", "N/A")
        category = event.get("category", "N/A")

        print(f"\n▶ Event [{event_id}] {event_title} ({category})")

        markets = event.get("markets", [])

        if not markets:
            print("  (No available markets)")
            continue

        print(f"  Available markets ({len(markets)}):")

        for market in markets:
            market_id = market.get("ticker", "N/A")
            market_title = market.get("yes_sub_title", "N/A")
            last_traded_price_yes = market.get("last_price_dollars", "N/A")
            outcome_prices = {
                "PriceYesBuy": market.get("yes_bid_dollars", "N/A"),
                "PriceNoBuy": market.get("no_bid_dollars", "N/A")
            }

            print(
                f"    - Market [{market_id}] {market_title} | "
                f"OrderBook: {outcome_prices} | "
                f"Yes_Chance: {last_traded_price_yes}"
            )

Found 14 sports: ['Football', 'Basketball', 'Hockey', 'Soccer', 'Tennis', 'Golf', 'MMA', 'Baseball', 'Boxing', 'Chess', 'Cricket', 'Esports', 'Motorsport', 'Olympics']


========== SPORT: Football ==========
Found 237 Football series tickers

▶ Event [KXNFLANYTD-26JAN25LASEA] Los Angeles R at Seattle: Anytime Touchdown Scorer (Sports)
  Available markets (19):
    - Market [KXNFLANYTD-26JAN25LASEA-LATATWELL5] Tutu Atwell | OrderBook: {'PriceYesBuy': '0.0400', 'PriceNoBuy': '0.9500'} | Yes_Chance: 0.0400
    - Market [KXNFLANYTD-26JAN25LASEA-SEASDARNOLD14] Sam Darnold | OrderBook: {'PriceYesBuy': '0.0800', 'PriceNoBuy': '0.9100'} | Yes_Chance: 0.0900
    - Market [KXNFLANYTD-26JAN25LASEA-SEARSHAHEED22] Rashid Shaheed | OrderBook: {'PriceYesBuy': '0.2100', 'PriceNoBuy': '0.7800'} | Yes_Chance: 0.2100
    - Market [KXNFLANYTD-26JAN25LASEA-SEAKWALKER9] Kenneth Walker III | OrderBook: {'PriceYesBuy': '0.5900', 'PriceNoBuy': '0.4000'} | Yes_Chance: 0.6000
    - Market [KXNFLANYTD-26JAN25LASE

### Ways to save the output in a CSV file to make it more readable

In [1]:
import requests
import pandas as pd

KALSHI_API = "https://api.elections.kalshi.com/trade-api/v2"

# -------- Initialize a list to collect data --------
data = []

# -------- FETCH ALL SPORTS --------
response = requests.get(f"{KALSHI_API}/search/filters_by_sport")
filters_data = response.json()
all_sports = [sport for sport in filters_data.get("sport_ordering", []) if sport != "All sports"]

print(f"Found {len(all_sports)} sports: {all_sports}")

# -------- LOOP OVER EACH SPORT --------
for sport in all_sports:
    print(f"\n\n========== SPORT: {sport} ==========")
    
    # -------- FETCH SERIES TICKERS FOR THIS SPORT --------
    response = requests.get(f"{KALSHI_API}/series", params={"category": "Sports", "tags": sport})
    series_data = response.json().get('series', [])
    sport_tickers = [s.get("ticker") for s in series_data if s.get("ticker")]
    
    print(f"Found {len(sport_tickers)} {sport} series tickers")
    
    # -------- FETCH EVENTS FOR EACH TICKER IN THIS SPORT --------
    all_events = []
    for ticker in sport_tickers:
        cursor = None
        limit = 200
        while True:
            params = {
                "status": "open",
                "series_ticker": ticker,
                "with_nested_markets": True,
                "limit": limit,
                "with_milestones": True
            }
            if cursor:
                params["cursor"] = cursor
            
            response = requests.get(f"{KALSHI_API}/events", params=params)
            data_response = response.json()
            events = data_response.get('events', [])
            
            if not events:
                break
            
            all_events.extend(events)
            cursor = data_response.get('cursor')
            if not cursor:
                break
    
    # -------- COLLECT EVENTS + MARKETS FOR THIS SPORT (instead of just printing) --------
    for event in all_events:
        event_id = event.get("event_ticker", "N/A")
        event_title = event.get("title", "N/A")
        category = event.get("category", "N/A")

        print(f"\n▶ Event [{event_id}] {event_title} ({category})")

        markets = event.get("markets", [])

        if not markets:
            print("  (No available markets)")
            continue

        print(f"  Available markets ({len(markets)}):")

        for market in markets:
            market_id = market.get("ticker", "N/A")
            market_title = market.get("yes_sub_title", "N/A")
            last_traded_price_yes = market.get("last_price_dollars", "N/A")
            outcome_prices = {
                "PriceYesBuy": market.get("yes_bid_dollars", "N/A"),
                "PriceNoBuy": market.get("no_bid_dollars", "N/A")
            }

            print(
                f"    - Market [{market_id}] {market_title} | "
                f"OrderBook: {outcome_prices} | "
                f"Yes_Chance: {last_traded_price_yes}"
            )
            
            # -------- APPEND TO DATA LIST (as per your snippet) --------
            data.append({
                'sport': sport,
                'event_id': event_id,
                'event_title': event_title,
                'category': category,
                'market_id': market_id,
                'market_title': market_title,
                'last_traded_price_yes': last_traded_price_yes,
                'PriceYesBuy': outcome_prices['PriceYesBuy'],
                'PriceNoBuy': outcome_prices['PriceNoBuy']
            })

# -------- SAVE TO DATAFRAME AND CSV --------
df = pd.DataFrame(data)
df.to_csv('kalshi_data.csv', index=False)
print(f"\nData saved to 'kalshi_data.csv' with {len(df)} rows.")

Found 15 sports: ['Football', 'Basketball', 'Hockey', 'Soccer', 'Tennis', 'Golf', 'MMA', 'Baseball', 'Boxing', 'Chess', 'Cricket', 'Esports', 'Motorsport', 'Olympics', 'Table Tennis']


========== SPORT: Football ==========
Found 235 Football series tickers

▶ Event [KXNFL2TD-26JAN25LASEA] Los Angeles R at Seattle: Two or More Touchdowns Scorer (Sports)
  Available markets (7):
    - Market [KXNFL2TD-26JAN25LASEA-SEARSHAHEED22] Rashid Shaheed | OrderBook: {'PriceYesBuy': '0.0200', 'PriceNoBuy': '0.9700'} | Yes_Chance: 0.0300
    - Market [KXNFL2TD-26JAN25LASEA-SEAKWALKER9] Kenneth Walker III | OrderBook: {'PriceYesBuy': '0.2000', 'PriceNoBuy': '0.7900'} | Yes_Chance: 0.2100
    - Market [KXNFL2TD-26JAN25LASEA-SEAJSMITHNJIGBA11] Jaxon Smith-Njigba | OrderBook: {'PriceYesBuy': '0.1300', 'PriceNoBuy': '0.8600'} | Yes_Chance: 0.1300
    - Market [KXNFL2TD-26JAN25LASEA-SEAABARNER88] AJ Barner | OrderBook: {'PriceYesBuy': '0.0300', 'PriceNoBuy': '0.9400'} | Yes_Chance: 0.0600
    - Market [K

In [2]:
import pandas as pd

# df already exists at this point

rows = []
event_index = 0

# Group by event
for (sport, event_id, event_title, category), group in df.groupby(
    ["sport", "event_id", "event_title", "category"],
    dropna=False
):
    event_index += 1

    # -------- EVENT ROW --------
    rows.append({
        "row_type": "EVENT",
        "event_index": event_index,
        "sport": sport,
        "event_id": event_id,
        "event_title": event_title,
        "category": category,
        "market_id": "",
        "market_title": "",
        "last_traded_price_yes": "",
        "PriceYesBuy": "",
        "PriceNoBuy": ""
    })

    # -------- MARKET ROWS --------
    for _, r in group.iterrows():
        rows.append({
            "row_type": "MARKET",
            "event_index": event_index,
            "sport": "",
            "event_id": "",
            "event_title": "",
            "category": "",
            "market_id": r["market_id"],
            "market_title": r["market_title"],
            "last_traded_price_yes": r["last_traded_price_yes"],
            "PriceYesBuy": r["PriceYesBuy"],
            "PriceNoBuy": r["PriceNoBuy"]
        })

# -------- FINAL CSV --------
df_hierarchical = pd.DataFrame(rows)
df_hierarchical.to_csv("kalshi_data_hierarchical.csv", index=False)

print(
    f"Saved kalshi_data_hierarchical.csv with "
    f"{event_index} events and {len(df_hierarchical)} rows."
)


Saved kalshi_data_hierarchical.csv with 1524 events and 10459 rows.
